# Neural search for question answering

The exercise introduces the problem of passage retrieval, an important step in factual question answering. This part concentrates on the methods for retrieving the content of documents that might be useful for answering the question. We compare lexical text representations (e.g. ElasticSearch default behaviour), with dense text representations (e.g. multilingual E5 neural model).

1. Read the documentation of the document store and the retriever in the Haystack framework.
2. Install Haystack framework (e.g. with pip install 'farm-haystack[all]').

In [ ]:
pip install 'farm-haystack[all]'

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.6/152.6 kB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.6/64.6 kB 2.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 44.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 800.5/800.5 kB 35.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 3.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.1/50.1 kB 4.0 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of weaviate-client to determine which version is compatible with other requirements. This could take a while.
INFO: pip is still looking at multiple versions of weaviate-client to determine which version is compa

3. Configure a document store based on Faiss supported by multilingual E5 model:
- For Faiss use multilingual E5 or silver retriever base encoder.
- Warning: If you use E5, make sure to properly configure the store.
- In the case you have problems using Faiss, you can use InMemoryDocumentStore, but this will require to re-index all documents each time the script is run, which is time consuming.

In [ ]:
from haystack.document_stores import FAISSDocumentStore
from haystack.nodes import EmbeddingRetriever
from haystack.nodes import DensePassageRetriever
from haystack.pipelines import DocumentSearchPipeline
from haystack.schema import Document

document_store.delete_documents()
document_store = FAISSDocumentStore(embedding_dim=768)  

retriever = DensePassageRetriever(
    document_store=document_store,
    query_embedding_model="ipipan/silver-retriever-base-v1",
    passage_embedding_model="ipipan/silver-retriever-base-v1"
)


4. Load the documents (passages) from the FiQA corpus.

In [ ]:
# pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 13.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 15.1 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2024.10.0
    Uninstalling fsspec-2024.10.0:
      Successfully uninstalled fsspec-2024.10.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2024.10.0 requires fsspec==2024.10.0, but you have fsspec 2024.9.0 which is incompatible.


In [ ]:
from datasets import load_dataset

queries_dataset = load_dataset("clarin-knext/fiqa-pl", "queries")
queries = queries_dataset['queries']
queries = queries.to_pandas()

qa_dataset = load_dataset("clarin-knext/fiqa-pl-qrels")
test_data = qa_dataset['test']
qrels = test_data.to_pandas()

corpus_dataset = load_dataset("clarin-knext/fiqa-pl", "corpus")
corpus = corpus_dataset['corpus']
corpus = corpus.to_pandas()

README.md:   0%|          | 0.00/201 [00:00<?, ?B/s]

fiqa-pl.py:   0%|          | 0.00/1.67k [00:00<?, ?B/s]

0000.parquet:   0%|          | 0.00/377k [00:00<?, ?B/s]

Generating queries split:   0%|          | 0/6648 [00:00<?, ? examples/s]

README.md:   0%|          | 0.00/201 [00:00<?, ?B/s]

...

Generating train split:   0%|          | 0/14166 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1238 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1706 [00:00<?, ? examples/s]

0000.parquet:   0%|          | 0.00/32.3M [00:00<?, ?B/s]

Generating corpus split:   0%|          | 0/57638 [00:00<?, ? examples/s]

In [ ]:
# Index documents
documents = []

for id, text in zip(corpus['_id'], corpus['text']):
  documents.append({
        'content': text,
        'meta': {'id': id}
    })

document_store.write_documents(documents)

Writing Documents: 60000it [02:08, 466.95it/s]


In [ ]:
document_store.update_embeddings(retriever)
pipe = DocumentSearchPipeline(retriever)

Create embeddings:  26%|██▌       | 2560/10000 [00:32<01:33, 79.18 Docs/s]

5. Use the set of questions and the scorings defined in this corpus, to compute NDCG@5 for the dense retriever.

In [ ]:
import numpy as np

def calc_ndcg_k(true, predicted):
    dcg = np.sum(predicted / np.log2(np.arange(2, len(true) + 2)))
    idcg = np.sum(true / np.log2(np.arange(2, len(true) + 2)))
    return dcg / idcg if idcg > 0 else 0

def calculate_average_ndcg(pipeline, questions, test_data, max_relevant_matches):
    total_ndcg = 0
    query_count = 0

    for query_id in test_data['query-id'].unique():
        question_row = questions[questions['_id'] == str(query_id)]
        if question_row.empty:
            continue

        query_text = "Pytanie: " + question_row.iloc[0]['text']

        search_results = pipeline.run(query=query_text, params={"Retriever": {"top_k": 5}})

        relevant_documents = set(test_data[test_data['query-id'] == query_id]['corpus-id'])

        relevant_count = min(max_relevant_matches.loc[query_id], 5)
        true_relevance = [1] * relevant_count + [0] * (5 - relevant_count)

        predicted_relevance = [
            1 if int(doc.meta['id']) in relevant_documents else 0
            for doc in search_results['documents'][:5]
        ]
        predicted_relevance += [0] * (5 - len(predicted_relevance))

        total_ndcg += calc_ndcg_k(true_relevance, predicted_relevance)
        query_count += 1

    return total_ndcg / query_count if query_count > 0 else 0


In [ ]:
max_relevant_matches = qrels.groupby('query-id')['corpus-id'].count().rename('count')

average_ndcg = calculate_average_ndcg(pipe, queries, qrels, max_relevant_matches)

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
print(f"Average NDCG@5: {average_ndcg}")

Average NDCG@5: 0.030539526459151693


6. Compare the NDCG score from this exercise with the score from lab 2 and from lab 6.